In [75]:
%matplotlib inline
import numpy as np
import pandas as pd
import matplotlib.pyplot as plt
import seaborn as sns
from sklearn.preprocessing import PowerTransformer,StandardScaler,LabelEncoder
from sklearn.model_selection import train_test_split,GridSearchCV,cross_val_score,KFold
from sklearn.impute import KNNImputer
from sklearn.pipeline import Pipeline
from sklearn.ensemble import RandomForestClassifier,GradientBoostingClassifier
from xgboost import XGBClassifier
from sklearn.decomposition import PCA
from sklearn.experimental import enable_halving_search_cv
from sklearn.model_selection import HalvingGridSearchCV,HalvingRandomSearchCV
from sklearn.metrics import confusion_matrix, classification_report,roc_curve,auc
import warnings
warnings.filterwarnings('ignore')

In [14]:
pd.options.display.max_columns=None
pd.options.display.max_rows=None

In [3]:
df=pd.read_csv('data.csv')
data=df.copy()
print(data.shape)
data.head()

(6819, 96)


Bankrupt?   ROA(C) before interest and depreciation before interest  \
0          1                                           0.370594          
1          1                                           0.464291          
2          1                                           0.426071          
3          1                                           0.399844          
4          1                                           0.465022          

    ROA(A) before interest and % after tax  \
0                                 0.424389   
1                                 0.538214   
2                                 0.499019   
3                                 0.451265   
4                                 0.538432   

    ROA(B) before interest and depreciation after tax  \
0                                           0.405750    
1                                           0.516730    
2                                           0.472295    
3                                           0.457733    
4                                           0.522298    

    Operating Gross Margin   Realized Sales Gross Margin  \
0                 0.601457                      0.601457   
1                 0.610235                      0.610235   
2                 0.601450                      0.601364   
3                 0.583541                      0.583541   
4                 0.598783                      0.598783   

    Operating Profit Rate   Pre-tax net Interest Rate  \
0                0.998969                    0.796887   
1                0.998946                    0.797380   
2                0.998857                    0.796403   
3                0.998700                    0.796967   
4                0.998973                    0.797366   

    After-tax net Interest Rate   Non-industry income and expenditure/revenue  \
0                      0.808809                                      0.302646   
1                      0.809301                                      0.303556   
2                      0.808388                                      0.302035   
3                      0.808966                                      0.303350   
4                      0.809304                                      0.303475   

   ...   Net Income to Total Assets   Total assets to GNP price  \
0  ...                     0.716845                    0.009219   
1  ...                     0.795297                    0.008323   
2  ...                     0.774670                    0.040003   
3  ...                     0.739555                    0.003252   
4  ...                     0.795016                    0.003878   

    No-credit Interval   Gross Profit to Sales  \
0             0.622879                0.601453   
1             0.623652                0.610237   
2             0.623841                0.601449   
3             0.622929                0.583538   
4             0.623521                0.598782   

    Net Income to Stockholder's Equity   Liability to Equity  \
0                             0.827890              0.290202   
1                             0.839969              0.283846   
2                             0.836774              0.290189   
3                             0.834697              0.281721   
4                             0.839973              0.278514   

    Degree of Financial Leverage (DFL)  \
0                             0.026601   
1                             0.264577   
2                             0.026555   
3                             0.026697   
4                             0.024752   

    Interest Coverage Ratio (Interest expense to EBIT)   Net Income Flag  \
0                                           0.564050                   1   
1                                           0.570175                   1   
2                                           0.563706                   1   
3                                           0.564663                   1   
4                        

In [16]:
data.describe()

Bankrupt?   ROA(C) before interest and depreciation before interest  \
count  6819.000000                                        6819.000000          
mean      0.032263                                           0.505180          
std       0.176710                                           0.060686          
min       0.000000                                           0.000000          
25%       0.000000                                           0.476527          
50%       0.000000                                           0.502706          
75%       0.000000                                           0.535563          
max       1.000000                                           1.000000          

        ROA(A) before interest and % after tax  \
count                              6819.000000   
mean                                  0.558625   
std                                   0.065620   
min                                   0.000000   
25%                                   0.535543   
50%                                   0.559802   
75%                                   0.589157   
max                                   1.000000   

        ROA(B) before interest and depreciation after tax  \
count                                        6819.000000    
mean                                            0.553589    
std                                             0.061595    
min                                             0.000000    
25%                                             0.527277    
50%                                             0.552278    
75%                                             0.584105    
max                                             1.000000    

        Operating Gross Margin   Realized Sales Gross Margin  \
count              6819.000000                   6819.000000   
mean                  0.607948                      0.607929   
std                   0.016934                      0.016916   
min                   0.000000                      0.000000   
25%                   0.600445                      0.600434   
50%                   0.605997                      0.605976   
75%                   0.613914                      0.613842   
max                   1.000000                      1.000000   

        Operating Profit Rate   Pre-tax net Interest Rate  \
count             6819.000000                 6819.000000   
mean                 0.998755                    0.797190   
std                  0.013010                    0.012869   
min                  0.000000                    0.000000   
25%                  0.998969                    0.797386   
50%                  0.999022                    0.797464   
75%                  0.999095                    0.797579   
max                  1.000000                    1.000000   

        After-tax net Interest Rate  \
count                   6819.000000   
mean                       0.809084   
std                        0.013601   
min                        0.000000   
25%                        0.809312   
50%                        0.809375   
75%                        0.809469   
max                        1.000000   

        Non-industry income and expenditure/revenue  \
count                                   6819.000000   
mean                                       0.303623   
std                                        0.011163   
min                                        0.000000   
25%                                        0.303466   
50%                                        0.303525   
75%                                        0.303585   
max                                        1.000000   

        Continuous interest rate (after tax)   Operating Expense Rate  \
count                            6819.000000             6.819000e+03   
mean                                0.781381             1.995347e+09   
std                                 0.012679             3.237684e+09   
min                 

In [17]:
data.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 6819 entries, 0 to 6818
Data columns (total 96 columns):
 #   Column                                                    Non-Null Count  Dtype  
---  ------                                                    --------------  -----  
 0   Bankrupt?                                                 6819 non-null   int64  
 1    ROA(C) before interest and depreciation before interest  6819 non-null   float64
 2    ROA(A) before interest and % after tax                   6819 non-null   float64
 3    ROA(B) before interest and depreciation after tax        6819 non-null   float64
 4    Operating Gross Margin                                   6819 non-null   float64
 5    Realized Sales Gross Margin                              6819 non-null   float64
 6    Operating Profit Rate                                    6819 non-null   float64
 7    Pre-tax net Interest Rate                                6819 non-null   float64
 8    After-tax net Int

In [15]:
data.isna().sum()

Bankrupt?                                                   0
 ROA(C) before interest and depreciation before interest    0
 ROA(A) before interest and % after tax                     0
 ROA(B) before interest and depreciation after tax          0
 Operating Gross Margin                                     0
 Realized Sales Gross Margin                                0
 Operating Profit Rate                                      0
 Pre-tax net Interest Rate                                  0
 After-tax net Interest Rate                                0
 Non-industry income and expenditure/revenue                0
 Continuous interest rate (after tax)                       0
 Operating Expense Rate                                     0
 Research and development expense rate                      0
 Cash flow rate                                             0
 Interest-bearing debt interest rate                        0
 Tax rate (A)                                               0
 Net Val

In [24]:
from pandas_profiling import ProfileReport
profile = ProfileReport(data,minimal=True)
profile

In [25]:
X=data.drop('Bankrupt?',axis=1)
y=data['Bankrupt?']

In [57]:
X_train, X_test, y_train, y_test = train_test_split(X, y,stratify=y, test_size=0.2, random_state=42)
print(X_train.shape, X_test.shape)

(5455, 95) (1364, 95)


In [58]:
pca=PCA()
pcademo = pd.DataFrame(pca.fit_transform(X_train))
demo = pcademo
demo.head()

0             1             2             3             4   \
0  6.813413e+09 -3.127431e+09  1.861537e+09 -1.364502e+09 -2.816042e+09   
1  4.290625e+09 -1.176285e+09 -1.507752e+09 -4.755982e+09  2.107141e+09   
2  6.095000e+08 -5.195471e+09  4.649652e+09 -2.966759e+07 -9.241535e+08   
3 -3.349644e+08 -2.200506e+09  9.168846e+08  2.808095e+09  1.504864e+09   
4 -2.937014e+09 -3.523494e+09 -2.692137e+09 -4.223824e+09  2.468274e+09   

             5             6             7             8             9   \
0 -8.222203e+08 -3.600173e+08  3.612250e+09 -7.592451e+07 -3.600858e+07   
1 -7.899566e+08 -5.138382e+08 -3.954541e+09 -7.526302e+07 -4.592225e+07   
2  4.137450e+08 -9.177758e+08 -7.350997e+08 -7.603803e+07 -7.133481e+07   
3 -2.908820e+09  6.171702e+07 -3.196672e+08 -8.608262e+07 -3.951513e+07   
4 -1.732548e+09 -5.873291e+08 -6.729368e+08 -1.273725e+08 -3.186956e+07   

             10            11            12            13            14  \
0 -7.954091e+07 -6.362756e+06  9.857509e+06 -2.178897e+07 -1.665145e+07   
1 -9.150904e+07 -4.824873e+07 -1.536922e+07 -2.463625e+07 -2.270672e+07   
2 -8.138105e+07 -3.326590e+06 -3.068634e+06  8.421108e+05  1.142905e+07   
3 -3.672706e+07 -1.462275e+07 -1.125846e+07 -1.686398e+07 -1.361204e+07   
4 -6.344609e+07 -7.192981e+07 -3.451059e+07 -2.841413e+07 -3.621241e+07   

             15            16            17            18            19  \
0 -1.430408e+06 -2.683943e+06  2.946013e+06  4.784909e+06 -1.469653e+07   
1 -1.749696e+07 -1.054080e+07 -4.400760e+06  5.293142e+06 -1.284510e+07   
2 -1.528894e+07 -2.448387e+06  1.664900e+06  2.356495e+06 -1.728984e+07   
3 -8.819799e+06 -1.042105e+07  1.419719e+06  1.231486e+06 -1.372272e+07   
4 -1.644876e+07 -1.391435e+07 -6.691855e+06  4.280934e+06 -2.062954e+07   

             20            21             22        23        24        25  \
0  6.118177e+05 -7.982266e+05  364749.819772  0.190886 -0.304317  0.115620   
1 -2.200435e+06 -1.152873e+06 -198547.052882 -0.270992  0.287710  0.008999   
2 -6.876577e+05 -1.132340e+06  713428.542452  0.119717  0.025648  0.125845   
3 -3.057008e+06 -9.463166e+05   -9415.580645 -0.535170  0.109541 -0.031949   
4 -5.946988e+06 -1.923919e+06 -252913.767602 -0.209813 -0.185318 -0.162494   

         26        27        28        29        30        31        32  \
0 -0.024292 -0.037040 -0.089528 -0.064726  0.029642  0.003008  0.001724   
1  0.221456  0.051436  0.157021 -0.106433  0.040143 -0.042124  0.027340   
2 -0.033375 -0.113808 -0.009220  0.005244  0.012305 -0.000651 -0.031802   
3  0.254457 -0.089578  0.046036 -0.030622 -0.092031 -0.055812  0.014378   
4 -0.069795 -0.160200 -0.022769 -0.335991 -0.069813 -0.013664  0.023516   

         33        34        35        36        37        38        39  \
0 -0.025388 -0.003821  0.004505  0.000022  0.007944 -0.012048  0.006195   
1 -0.011709 -0.000584 -0.003618 -0.004803 -0.013614  0.022983 -0.015382   
2 -0.004540 -0.012347  0.003468  0.004608  0.006996  0.004637 -0.003548   
3 -0.034325  0.016788  0.003439 -0.036940 -0.000356  0.007726 -0.003853   
4 -0.029538  0.045927 -0.054208  0.070101 -0.008710  0.012200 -0.003918   

         40        41        42        43        44        45        46  \
0  0.006802  0.004589 -0.006673 -0.000351  0.001811  0.001729 -0.003983   
1  0.010150 -0.006217  0.000268 -0.014960 -0.009182 -0.006052  0.002902   
2  0.006495  0.005293  0.001761 -0.008597  0.004369 -0.008537 -0.003101   
3 -0.001554  0.001454 -0.003428  0.003027 -0.004814  0.000432  0.001379   
4 -0.028023  0.098939  0.010978  0.038781 -0.038433 -0.037964  0.009295   

         47        48        49        50        51        52        53  \
0  0.005429 -0.000055  0.001224  0.000318 -0.002931 -0.004118  0.001203   
1 -0.007150  0.000299 -0.003922 -0.000602 -0.002663 -0.009076 -0.000260   
2  0.002595 -0.001350  0.007425  0.000796  0.001943  0.002308 -0.000909   
3 -0.001314  0.001044  0.006562 -0.005190 -0.012469 -0.006286 -0.000891   
4 -0.022972 

In [59]:
pca.explained_variance_ratio_

array([2.22172230e-01, 1.56583865e-01, 1.23630256e-01, 1.21680424e-01,
       1.10475148e-01, 9.07689907e-02, 8.50066107e-02, 6.95630167e-02,
       4.73915905e-03, 4.40256842e-03, 3.66969520e-03, 2.09647734e-03,
       1.15144327e-03, 1.09818759e-03, 9.69227991e-04, 7.81550259e-04,
       5.14234937e-04, 2.01355706e-04, 1.70518089e-04, 1.64090437e-04,
       1.30727257e-04, 2.69366090e-05, 3.28673420e-06, 1.56985871e-21,
       5.59323817e-22, 3.13328485e-22, 2.60967577e-22, 1.68874559e-22,
       1.06506915e-22, 8.90351958e-23, 5.58073207e-23, 4.37127312e-23,
       3.13203562e-23, 2.59836572e-23, 1.81793327e-23, 1.53783497e-23,
       1.47297837e-23, 1.16223927e-23, 9.21900158e-24, 8.89894612e-24,
       7.70414550e-24, 7.17263621e-24, 6.83512597e-24, 6.17914493e-24,
       5.72263886e-24, 5.18027761e-24, 4.21014286e-24, 4.14695534e-24,
       3.75034393e-24, 3.15459264e-24, 2.87983145e-24, 2.83704519e-24,
       2.55177159e-24, 2.06720364e-24, 1.90498329e-24, 1.76782672e-24,
      

In [60]:
total_var=np.cumsum(pca.explained_variance_ratio_)
total_var

array([0.22217223, 0.3787561 , 0.50238635, 0.62406678, 0.73454192,
       0.82531091, 0.91031752, 0.97988054, 0.9846197 , 0.98902227,
       0.99269196, 0.99478844, 0.99593988, 0.99703807, 0.9980073 ,
       0.99878885, 0.99930309, 0.99950444, 0.99967496, 0.99983905,
       0.99996978, 0.99999671, 1.        , 1.        , 1.        ,
       1.        , 1.        , 1.        , 1.        , 1.        ,
       1.        , 1.        , 1.        , 1.        , 1.        ,
       1.        , 1.        , 1.        , 1.        , 1.        ,
       1.        , 1.        , 1.        , 1.        , 1.        ,
       1.        , 1.        , 1.        , 1.        , 1.        ,
       1.        , 1.        , 1.        , 1.        , 1.        ,
       1.        , 1.        , 1.        , 1.        , 1.        ,
       1.        , 1.        , 1.        , 1.        , 1.        ,
       1.        , 1.        , 1.        , 1.        , 1.        ,
       1.        , 1.        , 1.        , 1.        , 1.     

In [61]:
pca=PCA(n_components=8)
Xtrain_pca=pd.DataFrame(pca.fit_transform(X_train))
Xtest_pca=pd.DataFrame(pca.transform(X_test))

In [62]:
rf=RandomForestClassifier(random_state=42,n_jobs=-1)
rf.fit(Xtrain_pca,y_train)
scores=cross_val_score(rf,Xtrain_pca,y_train,scoring='accuracy',cv=5,n_jobs=-1)
print(np.mean(scores))
print(rf.score(Xtest_pca,y_test))

0.9677360219981669
0.967741935483871


In [63]:
y_pred=rf.predict(Xtest_pca)
print(confusion_matrix(y_test,y_pred))
print(classification_report(y_test,y_pred))

[[1320    0]
 [  44    0]]
              precision    recall  f1-score   support

           0       0.97      1.00      0.98      1320
           1       0.00      0.00      0.00        44

    accuracy                           0.97      1364
   macro avg       0.48      0.50      0.49      1364
weighted avg       0.94      0.97      0.95      1364



In [67]:
rf_param={'criterion':['gini','entropy'],
          'max_depth':np.arange(2,50)}
gs_rf=HalvingRandomSearchCV(rf,param_distributions=rf_param,cv=5,resource='n_estimators',
                            max_resources=200,scoring='f1',n_jobs=-1)
gs_rf.fit(Xtrain_pca,y_train)
gs_rf.best_params_

{'max_depth': 43, 'criterion': 'entropy', 'n_estimators': 81}

In [65]:
rf1=RandomForestClassifier(criterion='entropy',max_depth=43,
                           n_estimators=81,random_state=42)
rf1.fit(Xtrain_pca,y_train)
scores=cross_val_score(rf1,Xtrain_pca,y_train,scoring='accuracy',cv=5,n_jobs=-1)
print(np.mean(scores))
print(rf1.score(Xtest_pca,y_test))

0.9677360219981669
0.967008797653959


In [66]:
y_pred=rf1.predict(Xtest_pca)
print(confusion_matrix(y_test,y_pred))
print(classification_report(y_test,y_pred))

[[1319    1]
 [  44    0]]
              precision    recall  f1-score   support

           0       0.97      1.00      0.98      1320
           1       0.00      0.00      0.00        44

    accuracy                           0.97      1364
   macro avg       0.48      0.50      0.49      1364
weighted avg       0.94      0.97      0.95      1364



In [68]:
pred_prob=rf1.predict_proba(Xtest_pca)
fpr,tpr,threshhold=roc_curve(y_test,pred_prob[:,1])
auc_=auc(fpr,tpr)
print(auc_)

0.7219696969696969


In [69]:
gb=GradientBoostingClassifier(random_state=42)
gb.fit(Xtrain_pca,y_train)
scores=cross_val_score(gb,Xtrain_pca,y_train,scoring='accuracy',cv=5,n_jobs=-1)
print(np.mean(scores))
print(gb.score(Xtest_pca,y_test))

0.9651695692025666
0.966275659824047


In [70]:
y_pred=gb.predict(Xtest_pca)
print(confusion_matrix(y_test,y_pred))
print(classification_report(y_test,y_pred))

[[1318    2]
 [  44    0]]
              precision    recall  f1-score   support

           0       0.97      1.00      0.98      1320
           1       0.00      0.00      0.00        44

    accuracy                           0.97      1364
   macro avg       0.48      0.50      0.49      1364
weighted avg       0.94      0.97      0.95      1364



In [71]:
gb_param={'loss':['deviance', 'exponential'],
          'max_depth':np.arange(2,50),
          'learning_rate': np.arange(0.01,1,0.01)}
gs_gb=HalvingRandomSearchCV(gb,param_distributions=gb_param,cv=5,resource='n_estimators',
                            max_resources=400,scoring='f1',n_jobs=-1)
gs_gb.fit(Xtrain_pca,y_train)
gs_gb.best_params_

{'max_depth': 22,
 'loss': 'deviance',
 'learning_rate': 0.92,
 'n_estimators': 243}

In [72]:
gb1=GradientBoostingClassifier(max_depth=22,loss='deviance',learning_rate= 0.92,n_estimators=243,random_state=42)
gb1.fit(Xtrain_pca,y_train)
scores=cross_val_score(gb1,Xtrain_pca,y_train,scoring='accuracy',cv=5,n_jobs=-1)
print(np.mean(scores))
print(gb1.score(Xtest_pca,y_test))

0.9527039413382218
0.9633431085043989


In [73]:
y_pred=gb1.predict(Xtest_pca)
print(confusion_matrix(y_test,y_pred))
print(classification_report(y_test,y_pred))

[[1313    7]
 [  43    1]]
              precision    recall  f1-score   support

           0       0.97      0.99      0.98      1320
           1       0.12      0.02      0.04        44

    accuracy                           0.96      1364
   macro avg       0.55      0.51      0.51      1364
weighted avg       0.94      0.96      0.95      1364



In [74]:
pred_prob=gb1.predict_proba(Xtest_pca)
fpr,tpr,threshhold=roc_curve(y_test,pred_prob[:,1])
auc_=auc(fpr,tpr)
print(auc_)

0.5974862258953167


In [76]:
xg=XGBClassifier()
xg.fit(Xtrain_pca,y_train)
scores=cross_val_score(xg,Xtrain_pca,y_train,scoring='accuracy',cv=5,n_jobs=-1)
print(np.mean(scores))
print(xg.score(Xtest_pca,y_test))

[14:13:00] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.4.0/src/learner.cc:1095: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
0.965352887259395
0.967008797653959


In [77]:
y_pred=xg.predict(Xtest_pca)
print(confusion_matrix(y_test,y_pred))
print(classification_report(y_test,y_pred))

[[1319    1]
 [  44    0]]
              precision    recall  f1-score   support

           0       0.97      1.00      0.98      1320
           1       0.00      0.00      0.00        44

    accuracy                           0.97      1364
   macro avg       0.48      0.50      0.49      1364
weighted avg       0.94      0.97      0.95      1364



In [78]:
xg_param={'gamma':np.arange(1,20),
          'max_depth':np.arange(2,50),
          'learning_rate': np.arange(0.01,1,0.01)}
gs_xg=HalvingRandomSearchCV(xg,param_distributions=xg_param,cv=5,resource='n_estimators',
                            max_resources=400,scoring='f1',n_jobs=-1)
gs_xg.fit(Xtrain_pca,y_train)
gs_xg.best_params_

[14:14:29] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.4.0/src/learner.cc:1095: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.


{'max_depth': 9, 'learning_rate': 0.76, 'gamma': 2, 'n_estimators': 243}

In [79]:
xg1=XGBClassifier(max_depth=9,gamma=2,learning_rate= 0.76,n_estimators=243)
xg1.fit(Xtrain_pca,y_train)
scores=cross_val_score(xg1,Xtrain_pca,y_train,scoring='accuracy',cv=5,n_jobs=-1)
print(np.mean(scores))
print(xg1.score(Xtest_pca,y_test))

[14:15:05] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.4.0/src/learner.cc:1095: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
0.9651695692025666
0.9611436950146628


In [80]:
y_pred=xg1.predict(Xtest_pca)
print(confusion_matrix(y_test,y_pred))
print(classification_report(y_test,y_pred))

[[1310   10]
 [  43    1]]
              precision    recall  f1-score   support

           0       0.97      0.99      0.98      1320
           1       0.09      0.02      0.04        44

    accuracy                           0.96      1364
   macro avg       0.53      0.51      0.51      1364
weighted avg       0.94      0.96      0.95      1364



In [81]:
pred_prob=xg1.predict_proba(Xtest_pca)
fpr,tpr,threshhold=roc_curve(y_test,pred_prob[:,1])
auc_=auc(fpr,tpr)
print(auc_)

0.665977961432507
